In [1]:
from matplotlib import pyplot as plt
from matplotlib.image import imread
import pandas as pd
from collections import Counter
import json
import os
import re
import tempfile
import numpy as np
from os.path import exists
from imblearn.under_sampling import RandomUnderSampler
from PIL import ImageFile
import sklearn as sk
from sklearn.model_selection import train_test_split, StratifiedShuffleSplit
import tensorflow as tf
import tensorflow.keras
from tensorflow.keras.preprocessing.image import ImageDataGenerator
from tensorflow.keras.layers import Conv2D, MaxPooling2D, Dense, Dropout, Flatten, Activation
from tensorflow.keras.models import Sequential
from tensorflow.keras.optimizers import Adam
# custom modules
import image_faults

ImageFile.LOAD_TRUNCATED_IMAGES = True

In [2]:
def add_regularization(model, regularizer=tf.keras.regularizers.l2(0.0001)):

    if not isinstance(regularizer, tf.keras.regularizers.Regularizer):
      print("Regularizer must be a subclass of tf.keras.regularizers.Regularizer")
      return model

    for layer in model.layers:
        for attr in ['kernel_regularizer']:
            if hasattr(layer, attr):
              setattr(layer, attr, regularizer)

    # When we change the layers attributes, the change only happens in the model config file
    model_json = model.to_json()

    # Save the weights before reloading the model.
    tmp_weights_path = os.path.join(tempfile.gettempdir(), 'tmp_weights.h5')
    model.save_weights(tmp_weights_path)

    # load the model from the config
    model = tf.keras.models.model_from_json(model_json)
    
    # Reload the model weights
    model.load_weights(tmp_weights_path, by_name=True)
    return model

In [3]:
# image_faults.faulty_images() # removes faulty images
df = pd.read_csv('expanded_class.csv', index_col=[0], low_memory=False)

In [4]:
def dict_pics():
    target_dir = os.getcwd() + os.sep + "training_images"
    with open('temp_pics_source_list.txt') as f:
        temp_pics_source_list = json.load(f)
    dict_pics = {k:target_dir + os.sep + re.search(r'[^/]+(?=/\$_|.jpg)', k, re.IGNORECASE).group() + '.jpg' for k in temp_pics_source_list}
    print("{source:target} dictionary created @ " + target_dir)
    return dict_pics

dict_pics = dict_pics()
blah = pd.Series(df.PictureURL)
df = df.drop(labels=['PictureURL'], axis=1)
blah = blah.apply(lambda x: dict_pics[x])
df = pd.concat([blah, df],axis=1)
df = df.groupby('PrimaryCategoryID').filter(lambda x: len(x)>25) # removes cat outliers
# removes non-existent image paths

{source:target} dictionary created @ /tf/training_images


In [5]:
df['PrimaryCategoryID'] = df['PrimaryCategoryID'].astype(str) # pandas thinks ids are ints

df=df.sample(frac=1)

In [6]:
undersample = RandomUnderSampler(sampling_strategy='auto')
train, y_under = undersample.fit_resample(df, df['PrimaryCategoryID'])
#print(Counter(train['PrimaryCategoryID']))

Counter({'11498': 3913, '11504': 3913, '11505': 3913, '11632': 3913, '15709': 3913, '24087': 3913, '45333': 3913, '53120': 3913, '53548': 3913, '53557': 3913, '55793': 3913, '62107': 3913, '95672': 3913})


In [7]:
train, test = train_test_split(train, test_size=0.2, random_state=42)
# stratify=train['PrimaryCategoryID']
# train['PrimaryCategoryID'].value_counts()

In [8]:
datagen = ImageDataGenerator(rescale=1./255., 
                             validation_split=.2,
                             #samplewise_std_normalization=True,
                             #horizontal_flip= True,
                             #vertical_flip= True,
                             #width_shift_range= 0.2,
                             #height_shift_range= 0.2,
                             #rotation_range= 90,
                             preprocessing_function=tf.keras.applications.vgg16.preprocess_input)
train_generator=datagen.flow_from_dataframe(
    dataframe=train[:len(train)],
    directory='./training_images',
    x_col='PictureURL',
    y_col='PrimaryCategoryID',
    batch_size=32,
    seed=42,
    shuffle=True,
    target_size=(244,244),
    subset='training'
    )
validation_generator=datagen.flow_from_dataframe(
    dataframe=train[:len(train)], # is using train right?
    directory='./training_images',
    x_col='PictureURL',
    y_col='PrimaryCategoryID',
    batch_size=32,
    seed=42,
    shuffle=True,
    target_size=(244,244),
    subset='validation'
    )

Found 32547 validated image filenames belonging to 13 classes.
Found 8136 validated image filenames belonging to 13 classes.


/usr/local/lib/python3.8/dist-packages/keras_preprocessing/image/dataframe_iterator.py:279: UserWarning: Found 12 invalid image filename(s) in x_col="PictureURL". These filename(s) will be ignored.
  warnings.warn(


In [9]:
imgs, labels = next(train_generator)

In [10]:
def plotImages(images_arr):
    fig, axes = plt.subplots(1, 10, figsize=(20,20))
    axes = axes.flatten()
    for img, ax in zip( images_arr, axes):
        ax.imshow(img)
        ax.axis('off')
    plt.tight_layout()
    plt.show()

In [11]:
#plotImages(imgs)
#print(labels)

In [12]:
physical_devices = tf.config.list_physical_devices('GPU')
print(len(physical_devices))
tf.config.experimental.set_memory_growth(physical_devices[0], True)

1


In [14]:
base_model = tf.keras.applications.vgg19.VGG19(weights='imagenet')

In [15]:
model = Sequential()
for layer in base_model.layers[:-1]:
    model.add(layer)

In [16]:
for layer in model.layers:
    layer.trainable = True
    
#model.add(Dropout(.5))
#model.add(Dense(64, activation='softmax'))
# model.add(Dropout(.25))

model.add(Dense(units=13, activation='softmax'))

In [18]:
#model = add_regularization(model)
model.summary()


Model: "sequential"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 block1_conv1 (Conv2D)       (None, 224, 224, 64)      1792      
                                                                 
 block1_conv2 (Conv2D)       (None, 224, 224, 64)      36928     
                                                                 
 block1_pool (MaxPooling2D)  (None, 112, 112, 64)      0         
                                                                 
 block2_conv1 (Conv2D)       (None, 112, 112, 128)     73856     
                                                                 
 block2_conv2 (Conv2D)       (None, 112, 112, 128)     147584    
                                                                 
 block2_pool (MaxPooling2D)  (None, 56, 56, 128)       0         
                                                                 
 block3_conv1 (Conv2D)       (None, 56, 56, 256)       2

In [19]:
model.compile(optimizer=Adam(learning_rate=.0001), loss='categorical_crossentropy',
              metrics=['accuracy'])
# sparse_categorical_crossentropy

In [20]:
model.fit(x=train_generator,
          steps_per_epoch=len(train_generator),
          validation_data=validation_generator,
          validation_steps=len(validation_generator),
          epochs=30,
          verbose=1)

Epoch 1/30
1018/1018 [==============================] - 391s 379ms/step - loss: 2.4329 - accuracy: 0.1571 - val_loss: 2.1902 - val_accuracy: 0.2525
Epoch 2/30
1018/1018 [==============================] - 379s 373ms/step - loss: 2.0578 - accuracy: 0.2960 - val_loss: 1.9160 - val_accuracy: 0.3330
Epoch 3/30
1018/1018 [==============================] - 381s 374ms/step - loss: 1.8221 - accuracy: 0.3681 - val_loss: 1.8588 - val_accuracy: 0.3535
Epoch 4/30
1018/1018 [==============================] - 383s 376ms/step - loss: 1.6406 - accuracy: 0.4272 - val_loss: 1.7819 - val_accuracy: 0.4028
Epoch 5/30
1018/1018 [==============================] - 383s 376ms/step - loss: 1.4577 - accuracy: 0.4920 - val_loss: 1.7216 - val_accuracy: 0.4158
Epoch 6/30
1018/1018 [==============================] - 379s 372ms/step - loss: 1.2528 - accuracy: 0.5607 - val_loss: 1.7924 - val_accuracy: 0.4140
Epoch 7/30
1018/1018 [==============================] - 378s 371ms/step - loss: 1.0030 - accuracy: 0.6469 - val_

KeyboardInterrupt: 